In [19]:
import copy, gtfs_functions
from tools.handlers.route_planner import Route_Planner
from tools.handlers.feed_handler import Feed_Handler
from tools.handlers.graph_handler import Graph_Handler

feed_handler = Feed_Handler(input_file='data/gtfs_zips/oebb_gtfs.zip')
graph_handler  = Graph_Handler()
G = graph_handler.read_graph('data/graphs/simple_graph_oebb.pickle')
route_planner = Route_Planner(feed=feed_handler.feed, G = G)

In [38]:
search = 'Wiener Neustadt Hauptbahnhof'
feed_handler.feed.stops.query("stop_name.str.contains('{}')".format(search))

stop_id                       stop_name   stop_lat   stop_lon  \
666   at:43:5210:0:1    Wiener Neustadt Hauptbahnhof  47.811004  16.233366   
667  at:43:5210:0:10    Wiener Neustadt Hauptbahnhof  47.811028  16.233249   
668  at:43:5210:0:11    Wiener Neustadt Hauptbahnhof  47.810974  16.233447   
669   at:43:5210:0:2    Wiener Neustadt Hauptbahnhof  47.810937  16.233689   
670   at:43:5210:0:3    Wiener Neustadt Hauptbahnhof  47.810956  16.233554   
671   at:43:5210:0:4    Wiener Neustadt Hauptbahnhof  47.810919  16.233779   
672   at:43:5210:0:5    Wiener Neustadt Hauptbahnhof  47.811058  16.233033   
673   at:43:5210:0:6    Wiener Neustadt Hauptbahnhof  47.811046  16.233114   
674   at:43:5210:0:7  Wiener Neustadt Hauptbahnhof A  47.812138  16.235153   
675   at:43:5210:0:8    Wiener Neustadt Hauptbahnhof  47.810696  16.233905   
676   at:43:5210:0:9    Wiener Neustadt Hauptbahnhof  47.810901  16.233923   

     zone_id                   geometry  
666      NaN  POINT (16.23337 47.81100)  
667      NaN  POINT (16.23325 47.81103)  
668      NaN  POINT (16.23345 47.81097)  
669      NaN  POINT (16.23369 47.81094)  
670      NaN  POINT (16.23355 47.81096)  
671      NaN  POINT (16.23378 47.81092)  
672      NaN  POINT (16.23303 47.81106)  
673      NaN  POINT (16.23311 47.81105)  
674      NaN  POINT (16.23515 47.81214)  
675      NaN  POINT (16.23390 47.81070)  
676      NaN  POINT (16.23392 47.81090)

In [42]:
start_station = 'Wiener Neustadt Hauptbahnhof'
df = copy.deepcopy(feed_handler.feed.stops)
df['travel_time'] = df.apply(lambda r: feed_handler.get_travel_time_from_graph(G=G, start_station=start_station, end_station=r['stop_name']) , axis=1)
df = df.loc[~df.travel_time.isnull()]
#gtfs_functions.map_gdf(gdf = df, variable='travel_time', tooltip_labels=['travel_time: '], tooltip_var=['travel_time'])

No success with station: Faak am See Bahnhof 1
Either source Wiener Neustadt Hauptbahnhof or target Faak am See Bahnhof 1 is not in G
No success with station: Klagenfurt West Bahnhst 1
Either source Wiener Neustadt Hauptbahnhof or target Klagenfurt West Bahnhst 1 is not in G
No success with station: Krumpendorf Bahnhof 1
Either source Wiener Neustadt Hauptbahnhof or target Krumpendorf Bahnhof 1 is not in G
No success with station: Pörtschach Bahnhof 1
Either source Wiener Neustadt Hauptbahnhof or target Pörtschach Bahnhof 1 is not in G
No success with station: Velden am Wörthersee Bahnhof 1
Either source Wiener Neustadt Hauptbahnhof or target Velden am Wörthersee Bahnhof 1 is not in G
No success with station: Villach Hbf 1
Either source Wiener Neustadt Hauptbahnhof or target Villach Hbf 1 is not in G
No success with station: Thörl-Maglern Bahnhof
Either source Wiener Neustadt Hauptbahnhof or target Thörl-Maglern Bahnhof is not in G
No success with station: St. Andrä Bahnhof 1
Either so

In [41]:
import folium

# Create a map object
m = folium.Map(location=[48, 16], zoom_start=7, clustered_marker=False)
cmap = LinearColormap(
    ['#00FF00', '#FFFF00', '#FFA500', '#FF0000'],
    vmin=df['travel_time'].min(),
    vmax=df['travel_time'].max()
)

# Add markers for each station
for _, row in df.iterrows():
    tooltip = f"{row['stop_name']} - {int(row['travel_time']/60)} min"
    color = 'green' if row['travel_time'] < 1800 else 'red'
    opacity = min(1, row['travel_time']/7200 + 0.2)
    folium.CircleMarker(
        location=[row['stop_lat'], row['stop_lon']],
        radius=2,        
        tooltip=['{}: {} min'.format(row['stop_name'], row['travel_time']/60)],
        fill=True,
        color=cmap(row['travel_time']),
        fill_opacity=0.8,
        fill_color=cmap(row['travel_time']),
        
        
    ).add_to(m)

# Show the map
m


In [32]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster
from branca.colormap import LinearColormap

# Load the data

# Create a colormap for travel times
cmap = LinearColormap(
    ['#00FF00', '#FFFF00', '#FFA500', '#FF0000'],
    vmin=df['travel_time'].min(),
    vmax=df['travel_time'].max()
)

# Create the map
m = folium.Map(location=[df['stop_lat'].mean(), df['stop_lon'].mean()], zoom_start=8, tiles='https://{s}.tile.openstreetmap.org/{z}/{x}/{y}.png', attr='Map data © <a href="https://openstreetmap.org">OpenStreetMap</a> contributors', clustered_marker=False)

# Add the markers to the map
mc = MarkerCluster()
for idx, row in df.iterrows():
    folium.CircleMarker(
        location=[row['stop_lat'], row['stop_lon']],
        radius=5,
        tooltip=row['stop_name'],
        fill=True,
        color=cmap(row['travel_time']),
        fill_opacity=0.8,
        fill_color=cmap(row['travel_time'])
    ).add_to(mc)
mc.add_to(m)

# Add the colormap to the map
cmap.caption = 'Travel time (seconds)'
cmap.add_to(m)

# Display the map
m
